EXTRACT DATA AND SAVE TO LOCAL DRIVE

In [7]:
import os
import openpyxl
import requests

In [19]:
# Function to extract data from excel file
def download_files_from_excel(file_path, download_folder):
    # Print the current working directory
    print("Current working directory:", os.getcwd())

    # Check if the file exists
    if not os.path.exists(file_path):
        print(f"File not found: {file_path}")
        return

    # Check if the download folder exists, if not, create it
    if not os.path.exists(download_folder):
        os.makedirs(download_folder)
        print(f"Created download folder: {download_folder}")
    else:
        print(f"Download folder already exists: {download_folder}")

    # Load the workbook and select the active worksheet
    workbook = openpyxl.load_workbook(file_path)
    sheet = workbook.active

    # Iterate through the rows in the worksheet and get the URLs
    for row in sheet.iter_rows(values_only=True):
        for url in row:
            if url and url.startswith('https://'):
                # Get the file name by splitting the URL
                file_name = url.split('/')[-1]

                # Send a GET request to the file URL
                response = requests.get(url)

                # Check if the request was successful
                if response.status_code == 200:
                    # Define the path to save the file
                    save_path = os.path.join(download_folder, file_name)

                    # Open the file in binary write mode and save the content
                    with open(save_path, 'wb') as file:
                        file.write(response.content)
                    print(f"Downloaded {file_name} to {save_path}") 
                else:
                    print(f"Failed to download {file_name}")

# Path to the Excel file containing the URLs
file_path = "/root/DataEngineeringScripts/notebooks/IBSA.xlsx"

# Path to the folder where the downloaded files will be saved
download_folder = "/root/DataEngineeringScripts/notebooks/IBSA_data"

# Call the function to download the files
download_files_from_excel(file_path, download_folder)

Current working directory: /root/DataEngineeringScripts/notebooks
Created download folder: /root/DataEngineeringScripts/notebooks/IBSA_data
Downloaded 12_Pilbara_DWERSuppliedFile.png to /root/DataEngineeringScripts/notebooks/IBSA_data/12_Pilbara_DWERSuppliedFile.png
Downloaded Metadata%20and%20Licensing%20Statement_updated.pdf to /root/DataEngineeringScripts/notebooks/IBSA_data/Metadata%20and%20Licensing%20Statement_updated.pdf
Downloaded Survey_Report_compressed.pdf to /root/DataEngineeringScripts/notebooks/IBSA_data/Survey_Report_compressed.pdf
Downloaded Survey_Report.txt to /root/DataEngineeringScripts/notebooks/IBSA_data/Survey_Report.txt
Downloaded ESRI%20Shapefile.zip to /root/DataEngineeringScripts/notebooks/IBSA_data/ESRI%20Shapefile.zip
Downloaded 14_Pilbara_DWERSuppliedFile.png to /root/DataEngineeringScripts/notebooks/IBSA_data/14_Pilbara_DWERSuppliedFile.png
Downloaded 0_Metadata%20and%20Licensing%20Statement_updated.pdf to /root/DataEngineeringScripts/notebooks/IBSA_data/

LOAD DATA TO AZURE STORAGE

In [2]:
from pathlib import Path
from PyPDF2 import PdfReader
from PIL import Image
import io
import zipfile
from azure.storage.blob import BlobClient, ContentSettings
import os
import shutil
import logging



In [6]:
# Setup logging to capture errors
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

# Function to ingest data to blob storage
def load_and_write_files(folder_path, container_url, sas_token, destination_path):
    # Check and convert folder to path if in string
    folder_path = Path(folder_path) if isinstance(folder_path, str) else folder_path
    
    # Iterate through the files in the folder and confirm if the files exist in the folder
    for file_path in folder_path.iterdir():
        if file_path.is_file():  # If file path exists in folder
            # Convert all the file extensions in the folder to lower case (case-insensitive), for easy handling
            file_extension = file_path.suffix.lower()
            # Connect to the blob storage using the API (generated url + token_key)
            blob_url_with_sas = f"{container_url}/{destination_path}/{file_path.name}{sas_token}"
            # Initiate the connection
            blob_client = BlobClient.from_blob_url(blob_url_with_sas)
            
            # Upload the various file extensions to the blob 
            try:
                if file_extension == '.txt':
                    with open(file_path, 'rb') as data:
                        blob_client.upload_blob(data, blob_type="BlockBlob", overwrite=True)  # Overwrite to prevent file duplicate
                elif file_extension == '.pdf':                                                # BlockBlob, for handling huge data
                    with open(file_path, 'rb') as data:
                        blob_client.upload_blob(data, blob_type="BlockBlob", overwrite=True, content_settings=ContentSettings(content_type='application/pdf')) # Ensure pdf are uploaded in their original format without distortion
                elif file_extension == '.png':
                    image = Image.open(file_path)
                    img_byte_arr = io.BytesIO() # Convert image to bytes to preserve it's originality
                    image.save(img_byte_arr, format='PNG')
                    blob_client.upload_blob(img_byte_arr.getvalue(), blob_type="BlockBlob", overwrite=True, content_settings=ContentSettings(content_type='image/png')) # Ensures Image files are uploaded in their original format without distortion
                elif file_extension == '.zip':
                    with open(file_path, 'rb') as data:
                        blob_client.upload_blob(data, blob_type="BlockBlob", overwrite=True, content_settings=ContentSettings(content_type='application/zip')) # Ensure Zip files are uploaded in their original format without distortion
                elif file_extension == '.mdb':
                    with open(file_path, 'rb') as data:
                        blob_client.upload_blob(data, blob_type="BlockBlob", overwrite=True)
                else:
                    logger.warning(f"Unsupported file type: {file_path.suffix}")
            except Exception as e:
                logger.error(f"Error processing file {file_path}: {e}")
        else:
            logger.info(f"Skipping directory: {file_path}")  # Else skip directory, if file path doesn't exist in folder

folder_path = r"/root/DataEngineeringScripts/notebooks/IBSA_data"
container_url = 'https://stproponentdata.blob.core.windows.net/ibsa'
sas_token = '?sv=2023-01-03&spr=https%2Chttp&st=2024-07-12T02%3A22%3A48Z&se=2024-07-19T02%3A22%3A00Z&sr=c&sp=rwl&sig=C0jXStedNSc0LkZ%2FHk0nHrQg%2BEr4yZHVlRgb%2BjtwFwc%3D' 
destination_path = 'cred.txt4' 

# Call the function to ingest data to the blob store
load_and_write_files(folder_path, container_url, sas_token, destination_path)

logger.info("All files have been loaded and written to the blob container.")

INFO:azure.core.pipeline.policies.http_logging_policy:Request URL: 'https://stproponentdata.blob.core.windows.net/ibsa/cred.txt4/IBSA-2020-0187.zip?sv=REDACTED&spr=REDACTED&st=REDACTED&se=REDACTED&sr=REDACTED&sp=REDACTED&sig=REDACTED'
Request method: 'PUT'
Request headers:
    'Content-Length': '1514568'
    'x-ms-blob-type': 'REDACTED'
    'x-ms-blob-content-type': 'REDACTED'
    'x-ms-version': 'REDACTED'
    'Content-Type': 'application/octet-stream'
    'Accept': 'application/xml'
    'User-Agent': 'azsdk-python-storage-blob/12.14.1 Python/3.10.12 (Linux-5.15.153.1-microsoft-standard-WSL2-x86_64-with-glibc2.35)'
    'x-ms-date': 'REDACTED'
    'x-ms-client-request-id': 'f23fea62-44b4-11ef-9477-2725cebecaa8'
A body is sent with the request
INFO:azure.core.pipeline.policies.http_logging_policy:Response status: 201
Response headers:
    'Content-Length': '0'
    'Content-MD5': 'REDACTED'
    'Last-Modified': 'Thu, 18 Jul 2024 03:22:23 GMT'
    'ETag': '"0x8DCA6D8D71F5109"'
    'Server

In [8]:


# Define the local path to the downloaded data file
#local_file_path = r"/root/DataEngineeringScripts/notebooks/IBSA_data/0_V2_1901_Snake%20Well_Flora%20Recon%20%26%20Fauna%20Level%201%20Assessment.txt"  # e.g., 'data/myfile.txt'

# Define Azure Blob Storage container URL and SAS token
#container_url = 'https://stproponentdata.blob.core.windows.net/ibsa'
#sas_token = '?sv=2023-01-03&spr=https%2Chttp&st=2024-07-12T02%3A22%3A48Z&se=2024-07-19T02%3A22%3A00Z&sr=c&sp=rwl&sig=C0jXStedNSc0LkZ%2FHk0nHrQg%2BEr4yZHVlRgb%2BjtwFwc%3D'

# Define the destination path within the blob container
#destination_path = 'cred.txt' 

# Create a write permission to the blob by combining url, token key and destination path
#blob_url_with_sas = f"{container_url}/{destination_path}{sas_token}"

# Initialize the BlobClient with the blob URL and SAS token
#blob_client = BlobClient.from_blob_url(blob_url_with_sas)

# Upload the file to the blob store
#with open(local_file_path, 'rb') as data:
    #blob_client.upload_blob(data, overwrite=True)  # Set overwrite=True if you want to overwrite existing blob

#print("File uploaded successfully.")